In [0]:
data = [
    ("Tahnik","Ahmed",'Raiyan',"M",2305),
    ("Esrak","Fardin","Ratul","M",9100),
    ("Rasel","Shikder","Rifat","F",2400),
    ("Sajib","Ahmed","Shobuj","M",14000),
    ("Sahria","Hossain","Sajjad","M",71000)

]
column = ["First_Name","Middle_Name","Last_Name","Gender","Salary"]
df1 = spark.createDataFrame(data = data,schema= column)


In [0]:
df1.show()

+----------+-----------+---------+------+------+
|First_Name|Middle_Name|Last_Name|Gender|Salary|
+----------+-----------+---------+------+------+
|    Tahnik|      Ahmed|   Raiyan|     M|  2305|
|     Esrak|     Fardin|    Ratul|     M|  9100|
|     Rasel|    Shikder|    Rifat|     F|  2400|
|     Sajib|      Ahmed|   Shobuj|     M| 14000|
|    Sahria|    Hossain|   Sajjad|     M| 71000|
+----------+-----------+---------+------+------+



In [0]:
import pyspark
from pyspark.sql import SparkSession 
from pyspark.sql.types import StructType, StructField, StringType, IntegerType



read data from csv and dbfs location 


In [0]:
df = spark.read.load("/FileStore/tables/googleplaystore-3.csv",format= 'csv',sep= ',',header = 'true',inferschema = True,escape = '"' )


In [0]:
df.count()

Out[46]: 10841

In [0]:
df.show(2)

+--------------------+--------------+------+-------+----+--------+----+-----+--------------+--------------------+----------------+-----------+------------+
|                 App|      Category|Rating|Reviews|Size|Installs|Type|Price|Content Rating|              Genres|    Last Updated|Current Ver| Android Ver|
+--------------------+--------------+------+-------+----+--------+----+-----+--------------+--------------------+----------------+-----------+------------+
|Photo Editor & Ca...|ART_AND_DESIGN|   4.1|    159| 19M| 10,000+|Free|    0|      Everyone|        Art & Design| January 7, 2018|      1.0.0|4.0.3 and up|
| Coloring book moana|ART_AND_DESIGN|   3.9|    967| 14M|500,000+|Free|    0|      Everyone|Art & Design;Pret...|January 15, 2018|      2.0.0|4.0.3 and up|
+--------------------+--------------+------+-------+----+--------+----+-----+--------------+--------------------+----------------+-----------+------------+
only showing top 2 rows



In [0]:
df.printSchema()

root
 |-- App: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Rating: double (nullable = true)
 |-- Reviews: string (nullable = true)
 |-- Size: string (nullable = true)
 |-- Installs: string (nullable = true)
 |-- Type: string (nullable = true)
 |-- Price: string (nullable = true)
 |-- Content Rating: string (nullable = true)
 |-- Genres: string (nullable = true)
 |-- Last Updated: string (nullable = true)
 |-- Current Ver: string (nullable = true)
 |-- Android Ver: string (nullable = true)



Data Celaning 

In [0]:
df = df.drop('Last Updated','Size','Content Rating','Current Ver')

In [0]:
df.show(2)

+--------------------+--------------+------+-------+--------+----+-----+--------------------+------------+
|                 App|      Category|Rating|Reviews|Installs|Type|Price|              Genres| Android Ver|
+--------------------+--------------+------+-------+--------+----+-----+--------------------+------------+
|Photo Editor & Ca...|ART_AND_DESIGN|   4.1|    159| 10,000+|Free|    0|        Art & Design|4.0.3 and up|
| Coloring book moana|ART_AND_DESIGN|   3.9|    967|500,000+|Free|    0|Art & Design;Pret...|4.0.3 and up|
+--------------------+--------------+------+-------+--------+----+-----+--------------------+------------+
only showing top 2 rows



Changing the datatypes of the columns 

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import regexp_replace, col
from pyspark.sql.types import IntegerType
df = df.withColumn("Reviews",col("Reviews").cast(IntegerType()))\
  .withColumn("Installs",regexp_replace(col("Installs"), "[^0-9]", ""))\
      .withColumn("Installs",col("Installs").cast(IntegerType()))\
          .withColumn("Price",col("Price").cast(IntegerType()))
  


In [0]:
df.show(2)

+--------------------+--------------+------+-------+--------+----+-----+--------------------+------------+
|                 App|      Category|Rating|Reviews|Installs|Type|Price|              Genres| Android Ver|
+--------------------+--------------+------+-------+--------+----+-----+--------------------+------------+
|Photo Editor & Ca...|ART_AND_DESIGN|   4.1|    159|   10000|Free|    0|        Art & Design|4.0.3 and up|
| Coloring book moana|ART_AND_DESIGN|   3.9|    967|  500000|Free|    0|Art & Design;Pret...|4.0.3 and up|
+--------------------+--------------+------+-------+--------+----+-----+--------------------+------------+
only showing top 2 rows



implementing sql on the pyspark dataframe 

In [0]:
df.createOrReplaceTempView('app')

In [0]:
%sql select * from app

App Category Rating Reviews Installs Type Price Genres Android Ver Photo Editor & Candy Camera & Grid & ScrapBook ART_AND_DESIGN 4.1 159 10000 Free 0 Art & Design 4.0.3 and up Coloring book moana ART_AND_DESIGN 3.9 967 500000 Free 0 Art & Design;Pretend Play 4.0.3 and up U Launcher Lite – FREE Live Cool Themes, Hide Apps ART_AND_DESIGN 4.7 87510 5000000 Free 0 Art & Design 4.0.3 and up Sketch - Draw & Paint ART_AND_DESIGN 4.5 215644 50000000 Free 0 Art & Design 4.2 and up Pixel Draw - Number Art Coloring Book ART_AND_DESIGN 4.3 967 100000 Free 0 Art & Design;Creativity 4.4 and up Paper flowers instructions ART_AND_DESIGN 4.4 167 50000 Free 0 Art & Design 2.3 and up Smoke Effect Photo Maker - Smoke Editor ART_AND_DESIGN 3.8 178 50000 Free 0 Art & Design 4.0.3 and up Infinite Painter ART_AND_DESIGN 4.1 36815 1000000 Free 0 Art & Design 4.2 and up Garden Coloring Book ART_AND_DESIGN 4.4 13791 1000000 Free 0 Art & Design 3.0 and up Kids Paint Free - Drawing Fun ART_AND_DESIGN 4.7 121 10000 Free 0 Art & Design;Creativity 4.0.3 and up Text on Photo - Fonteee ART_AND_DESIGN 4.4 13880 1000000 Free 0 Art & Design 4.1 and up Name Art Photo Editor - Focus n Filters ART_AND_DESIGN 4.4 8788 1000000 Free 0 Art & Design 4.0 and up Tattoo Name On My Photo Editor ART_AND_DESIGN 4.2 44829 10000000 Free 0 Art & Design 4.1 and up Mandala Coloring Book ART_AND_DESIGN 4.6 4326 100000 Free 0 Art & Design 4.4 and up 3D Color Pixel by Number - Sandbox Art Coloring ART_AND_DESIGN 4.4 1518 100000 Free 0 Art & Design 2.3 and up Learn To Draw Kawaii Characters ART_AND_DESIGN 3.2 55 5000 Free 0 Art & Design 4.2 and up Photo Designer - Write your name with shapes ART_AND_DESIGN 4.7 3632 500000 Free 0 Art & Design 4.1 and up 350 Diy Room Decor Ideas ART_AND_DESIGN 4.5 27 10000 Free 0 Art & Design 2.3 and up FlipaClip - Cartoon animation ART_AND_DESIGN 4.3 194216 5000000 Free 0 Art & Design 4.0.3 and up ibis Paint X ART_AND_DESIGN 4.6 224399 10000000 Free 0 Art & Design 4.1 and up Logo Maker - Small Business ART_AND_DESIGN 4.0 450 100000 Free 0 Art & Design 4.1 and up Boys Photo Editor - Six Pack & Men's Suit ART_AND_DESIGN 4.1 654 100000 Free 0 Art & Design 4.0.3 and up Superheroes Wallpapers | 4K Backgrounds ART_AND_DESIGN 4.7 7699 500000 Free 0 Art & Design 4.0.3 and up Mcqueen Coloring pages ART_AND_DESIGN NaN 61 100000 Free 0 Art & Design;Action & Adventure 4.1 and up HD Mickey Minnie Wallpapers ART_AND_DESIGN 4.7 118 50000 Free 0 Art & Design 4.1 and up Harley Quinn wallpapers HD ART_AND_DESIGN 4.8 192 10000 Free 0 Art & Design 3.0 and up Colorfit - Drawing & Coloring ART_AND_DESIGN 4.7 20260 500000 Free 0 Art & Design;Creativity 4.0.3 and up Animated Photo Editor ART_AND_DESIGN 4.1 203 100000 Free 0 Art & Design 4.0.3 and up Pencil Sketch Drawing ART_AND_DESIGN 3.9 136 10000 Free 0 Art & Design 2.3 and up Easy Realistic Drawing Tutorial ART_AND_DESIGN 4.1 223 100000 Free 0 Art & Design 2.3 and up Pink Silver Bow Keyboard Theme ART_AND_DESIGN 4.2 1120 100000 Free 0 Art & Design 4.0.3 and up Art Drawing Ideas ART_AND_DESIGN 4.1 227 50000 Free 0 Art & Design 2.3 and up Anime Manga Coloring Book ART_AND_DESIGN 4.5 5035 100000 Free 0 Art & Design 4.0 and up Easy Origami Ideas ART_AND_DESIGN 4.2 1015 100000 Free 0 Art & Design 4.1 and up I Creative Idea ART_AND_DESIGN 4.7 353 10000 Free 0 Art & Design 4.1 and up How to draw Ladybug and Cat Noir ART_AND_DESIGN 3.8 564 100000 Free 0 Art & Design 4.1 and up UNICORN - Color By Number & Pixel Art Coloring ART_AND_DESIGN 4.7 8145 500000 Free 0 Art & Design;Creativity 4.4 and up Floor Plan Creator ART_AND_DESIGN 4.1 36639 5000000 Free 0 Art & Design 2.3.3 and up PIP Camera - PIP Collage Maker ART_AND_DESIGN 4.7 158 10000 Free 0 Art & Design 4.0.3 and up How To Color Disney Princess - Coloring Pages ART_AND_DESIGN 4.0 591 500000 Free 0 Art & Design 4.0 and up Drawing Clothes Fashion Ideas ART_AND_DESIGN 4.2 117 10000 Free 0 Art & Design 4.0.3 and up Sad Poetry Photo Frames 2018 ART_AND_DESIGN 4.5 176 100000 Free 0 A

Finding the app with top reviews 

In [0]:
%sql select * from app
order by Reviews desc 
limit 10;

App Category Rating Reviews Installs Type Price Genres Android Ver Facebook SOCIAL 4.1 78158306 1000000000 Free 0 Social Varies with device Facebook SOCIAL 4.1 78128208 1000000000 Free 0 Social Varies with device WhatsApp Messenger COMMUNICATION 4.4 69119316 1000000000 Free 0 Communication Varies with device WhatsApp Messenger COMMUNICATION 4.4 69119316 1000000000 Free 0 Communication Varies with device WhatsApp Messenger COMMUNICATION 4.4 69109672 1000000000 Free 0 Communication Varies with device Instagram SOCIAL 4.5 66577446 1000000000 Free 0 Social Varies with device Instagram SOCIAL 4.5 66577313 1000000000 Free 0 Social Varies with device Instagram SOCIAL 4.5 66577313 1000000000 Free 0 Social Varies with device Instagram SOCIAL 4.5 66509917 1000000000 Free 0 Social Varies with device Messenger – Text and Video Chat for Free COMMUNICATION 4.0 56646578 1000000000 Free 0 Communication Varies with device

In [0]:
%sql select App , sum(Reviews) as TotalReview, avg(Rating) as Average_Rating
from app
group by app
order by TotalReview Desc
limit 10;

App TotalReview Average_Rating Instagram 266241989 4.5 WhatsApp Messenger 207348304 4.4 Clash of Clans 179558781 4.6 Messenger – Text and Video Chat for Free 169932272 4.0 Subway Surfers 166331958 4.5 Candy Crush Saga 156993136 4.3999999999999995 Facebook 156286514 4.1 8 Ball Pool 99386198 4.5 Clash Royale 92530298 4.6 Snapchat 68045010 4.0

Top Installed Apps

In [0]:
%sql select App , sum (installs) as Total_Installation 
from app 
group by 1 
order by 2 Desc;

App Total_Installation Subway Surfers 6000000000 Instagram 4000000000 Hangouts 4000000000 Google Drive 4000000000 Google News 4000000000 Google Photos 4000000000 Candy Crush Saga 3500000000 Google Chrome: Fast & Secure 3000000000 WhatsApp Messenger 3000000000 Messenger – Text and Video Chat for Free 3000000000 Gmail 3000000000 Maps - Navigate & Explore 3000000000 Skype - free IM & video calls 3000000000 Temple Run 2 3000000000 Viber Messenger 2500000000 YouTube 2000000000 Google Street View 2000000000 Snapchat 2000000000 Pou 2000000000 Google 2000000000 Google Play Games 2000000000 Google+ 2000000000 imo free video calls and chat 2000000000 Facebook 2000000000 Dropbox 1500000000 LINE: Free Calls & Messages 1500000000 Gboard - the Google Keyboard 1500000000 UC Browser - Fast Download Private & Secure 1500000000 Google Calendar 1500000000 Flipboard: News For Our Time 1500000000 MX Player 1500000000 Twitter 1500000000 My Talking Tom 1500000000 Microsoft Word 1500000000 Google Play Books 1000000000 SHAREit - Transfer & Share 1000000000 Google Play Movies & TV 1000000000 Google Duo - High Quality Video Calls 1000000000 Facebook Lite 1000000000 Google Translate 1000000000 ROBLOX 900000000 8 Ball Pool 700000000 Duolingo: Learn Languages Free 700000000 Sniper 3D Gun Shooter: Free Shooting Games - FPS 600000000 Helix Jump 600000000 slither.io 600000000 Farm Heroes Saga 500000000 Angry Birds Classic 500000000 Zombie Tsunami 500000000 TripAdvisor Hotels Flights Restaurants Attractions 500000000 Clean Master- Space Cleaner & Antivirus 500000000 Flow Free 500000000 Security Master - Antivirus, VPN, AppLock, Booster 500000000 Wish - Shopping Made Fun 500000000 BeautyPlus - Easy Photo Editor & Selfie Camera 500000000 Cloud Print 500000000 Samsung Health 500000000 eBay: Buy & Sell this Summer - Discover Deals Now! 500000000 Plants vs. Zombies FREE 500000000 Netflix 500000000 Clash Royale 400000000 Talking Tom Gold Run 400000000 Cymera Camera- Photo Editor, Filter,Collage,Layout 400000000 Garena Free Fire 400000000 My Talking Angela 400000000 ZEDGE™ Ringtones & Wallpapers 400000000 Evernote – Organizer, Planner for Notes & Memos 400000000 Google Pay 400000000 Angry Birds Rio 400000000 Badoo - Free Chat & Dating App 400000000 Hill Climb Racing 400000000 AliExpress - Smarter Shopping, Better Living 400000000 WeChat 400000000 Clash of Clans 400000000 Google Keep 400000000 Minion Rush: Despicable Me Official Game 400000000 Dream League Soccer 2018 300000000 Amazon Shopping 300000000 KakaoTalk: Free Calls & Text 300000000 Camera360: Selfie Photo Editor with Funny Sticker 300000000 Firefox Browser fast & private 300000000 Yahoo Mail – Stay Organized 300000000 Opera Mini - fast web browser 300000000 ES File Explorer File Manager 300000000 Tumblr 300000000 Candy Crush Soda Saga 300000000 Adobe Acrobat Reader 300000000 Cut the Rope FULL FREE 300000000 YouCam Perfect - Selfie Photo Editor 300000000 Google Docs 300000000 Opera Browser: Fast and Secure 300000000 UC Browser Mini -Tiny Fast Private & Secure 300000000 Score! Hero 300000000 Microsoft OneNote 300000000 IMDb Movies & TV 300000000 Telegram 300000000 Booking.com Travel Deals 300000000 Pinterest 300000000 B612 - Beauty & Filter Camera 300000000 Bowmasters 300000000 Candy Camera - selfie, beauty camera, photo editor 300000000 Hungry Shark Evolution 300000000 MeetMe: Chat & Meet New People 250000000 Calorie Counter - MyFitnessPal 250000000 Granny 250000000 Magic Tiles 3 200000000 Google Earth 200000000 CM Launcher 3D - Theme, Wallpapers, Efficient 200000000 Photo Editor Pro 200000000 Cooking Fever 200000000 Hill Climb Racing 2 200000000 Talking Ben the Dog 200000000 Android Messages 200000000 ColorNote Notepad Notes 200000000 Backgrounds HD (Wallpapers) 200000000 GO Keyboard - Emoticon keyboard, Free Theme, GIF 200000000 Sonic Dash 200000000 Messenger Lite: Free Calls & Messages 200000000 Waze - GPS, Maps, Traffic Alerts & Live Navigation 200000000 Crossy Road 200000000 PAC-MAN 200000000 Traffic Rac

Catgeory Wise Installation 

In [0]:
%sql select Category , sum(installs)
from app 
group by 1
order by 2 desc;

Category sum(installs) GAME 35086024415 COMMUNICATION 32647276251 PRODUCTIVITY 14176091369 SOCIAL 14069867902 TOOLS 11452771915 FAMILY 10258263505 PHOTOGRAPHY 10088247655 NEWS_AND_MAGAZINES 7496317760 TRAVEL_AND_LOCAL 6868887146 VIDEO_PLAYERS 6222002720 SHOPPING 3247848785 ENTERTAINMENT 2869160000 PERSONALIZATION 2325494782 BOOKS_AND_REFERENCE 1921469576 SPORTS 1751174498 HEALTH_AND_FITNESS 1583072512 BUSINESS 1001914865 FINANCE 876648734 EDUCATION 871452000 MAPS_AND_NAVIGATION 724281890 LIFESTYLE 537643539 WEATHER 426100520 FOOD_AND_DRINK 273898751 DATING 264310807 HOUSE_AND_HOME 168712461 ART_AND_DESIGN 124338100 LIBRARIES_AND_DEMO 62995910 COMICS 56086150 MEDICAL 53257437 AUTO_AND_VEHICLES 53130211 PARENTING 31521110 BEAUTY 27197050 EVENTS 15973161 1.9 null

Databricks visualization. Run in Databricks to view.

top paid apps 

In [0]:
%sql select App , sum(Price)
from app 
where Type = 'Paid'
group by 1
order by 2 desc; 

App sum(Price) I am Rich Plus null Trine 2: Complete Story null Whoowasit? - Best kids game! null AF-STROKE null Sokoban Land DX null Servidor Privado CR y CoC - Royale Servers PRO null Campervan.Guide Pro null XCOM®: Enemy Within null SweetLand — Family Board Game null Medical ID - In Case of Emergency (ICE) null Language Therapy: Aphasia null The World Ends With You null iHunter BC null Flipped Out! - Powerpuff Girls null Dr. Panda Restaurant 2 null Al'Quran Bahasa Indonesia PRO null Eu Sou Rico null bpresso PRO null CN Superstar Soccer: Goal!!! null Dz kayas null NBA JAM by EA SPORTS™ null FJ Toolkit null G-Force Driving Assistant null iFish BC null Dr. Panda's Swimming Pool null Be the Expert in Phlebotomy - Professional Nursing null pretty Easy privacy p≡p null MultiPicture Live Wallpaper dn null Electrician Calculator Pro null My Budget Book null ACCDB MDB DB Manager Pro - Editor for MS Access null AC DC Power Monitor null DR.MEEP null WIZARD Card Game null Ad Removal: thereisonlywe null DK Primrose for KLWP null Smart Wi-Fi Hotspot PRO null AJ Gray Dark Icon Pack null My Movies Pro - Movie & TV Collection Library null F05WatchFace for Android Wear null Morse Machine for Ham Radio null CZ-27 pistol explained null ZOOKEEPER DX TouchEdition null G-NetReport Pro null Guns'n'Glory Premium null Guns'n'Glory WW2 Premium null I am Rich Person null Ain Arabic Kids Alif Ba ta null Socle Commun BO du 23-04-2015 null Arrhythmias and Dysrhythmias null Hitman Sniper null Next Launcher 3D Theme Hit-G null FORD V SERIES CALC - NO LIMIT null Light X - Icon Pack null I AM RICH PRO PLUS null Técnico Legislativo Câmara Legislativa DF null myGrow null VeinSeek null Battleheart Legacy null Poker Equity Calculator Pro for No Limit Hold'em null FN model 1900 pistol explained null Dr. Panda Hospital null ExDialer PRO Key null My Little Work – Garage null New York Mysteries (Full) null Skip-Bo™ null go41cx null Nighty Night Circus null ASCCP Mobile null Weather Forecast Pro null League of Stickman 2018- Ninja Arena PVP(Dreamsky) null AP Series Solution Pro null BSPlayer null CE Genius Nurses Edition null An Elite Warrior Ex null Fruit Ninja Classic null Minecraft null Math games for kids : times tables training null Golfshot Plus: Golf GPS null I Am Rich null Es-Bg Offline Voice Translator null DW Contacts widget null Glanceable Ap Watch Face null I'm Rich/Eu sou Rico/أنا غني/我很有錢 null BeFunky Photo Editor Pro null MEGA MAN MOBILE null IBM Micromedex Drug Info null W Pro - Weather Forecast & Animated Weather Maps null Power Widget null Wi-Fi Rabbit Unlock Key null MyRadar NOAA Weather Radar Ad Free null ZombieVital DG null aCalendar+ Calendar & Tasks null Alarmy (Sleep If U Can) - Pro null AP Art History Flashcards null Ad Blocker for SayHi null Muscle Trigger Point Anatomy null DRAGON QUEST V null Nightenfell: Shared AR null AH Alarm Panel null I Am Rich Premium null BL 1-Click Camera null BP Fitness Lead Scanner null CW Beacon for Ham Radio null Police Field Interview FI Card null FN FAL rifle explained null Ai-Ball AV Recorder null Menstrual Calendar Premium null S Launcher Pro for Galaxy null cronometer (ad free) null Michael's AG Sound Board null The EO Bar null J Alvarej Moji null Android P | Xperia™ Theme 4800+ icons null Toca Life: City null Toca Builders null SkyTest BU/GU Lite null Teen Titans GO Figure! null Facetune - For Free null Ulysse Speedometer Pro null AJ Orange Icon Pack null Gravidez ao Vivo null Puffin Browser Pro null Android P Home KLWP null The Game of Life null DraStic DS Emulator null Moco+ - Chat, Meet People null Chess and Mate null Pacify Exceed (Android P) - Theme for Xperia™ null Age of AI: War Strategy null Differential Dx null Essential Anatomy 3 null My Virtual Boyfriend null Prime Key for Nougat Launcher& O Launcher &KitKat null Pujie Black Watch Face for Android Wear OS null BackCountry Navigator TOPO GPS PRO null Bitcoin BX Thailand PRO null Active Soccer 2 DX null Advanced EX for RENAULT null All-night drug

In [0]:
%sql select distinct Type from app

Type 0 NaN Free Paid